In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline  

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.offline as pl
pl.init_notebook_mode(connected=True)
import plotly.graph_objs as go

from datetime import datetime, timedelta
import parseIntervalFiles as pif
import parseActivityFiles as paf
#pun intended :)
import consolidateFiles as cf
import datacleaning as cl
import dataviz as dv

In [2]:
verbose = True

PATH = "C:\\Users\\ju\\GDrive\\Projects\\HeRV\\Data\\"
RAW = PATH + "Raw"

In [3]:
file = PATH + "PreProcessed\\sessions.xlsx"
df = pd.read_excel(file)
print(len(df), 'sessions read')
df = df.sort_values(by='sess_id', ascending=True)
df.head(3)

461 sessions read


activity  beatscount  duration            hf       hfnu           lf  \
0  focused-active        2862      2975  16632.760739  68.597096  7614.272703   
1         leisure         484       520  13446.858350  76.104324  4222.122427   
2             eat         269       202   6220.909893  67.226302  3032.774584   

      lf_hf       lfnu        mhr         mrri   ...     posture  \
0  0.457788  31.402904  60.349820  1061.744934   ...         sit   
1  0.313986  23.895676  56.160275  1096.966942   ...         sit   
2  0.487513  32.773698  83.980195   760.349442   ...         sit   

  removed_artifacts       rmssd        sdnn               start  \
0                25  239.316870  233.739654 2017-09-29 12:25:28   
1                 0  215.915390  172.462601 2017-09-29 13:20:00   
2                 4  158.107901  160.693497 2017-09-29 13:32:20   

                 stop   total_power user          vlf  sess_id  
0 2017-09-29 13:15:03  29488.443381    0  5241.409939        0  
1 2017-09-29 13:28:40  20709.546077    0  3040.565300        1  
2 2017-09-29 13:35:42  12481.494769    0  3227.810292        2  

[3 rows x 23 columns]

In [4]:
fdf = pd.read_excel(PATH+ 'PreProcessed/df_60_0.xlsx')

## Plotting random examples of RR time series for each type of activity

In [5]:
for act in df['activity'].unique():
    v = df[df['activity'] == act].sample(1)
    for i in range(1):
        dv.full_plot_sess(v.iloc[0], fdf, RAW)

SESSION ID:  70
ACTIVITY:  focused-active
USER:  0
TIME:  2017-10-14 03:31:57


SESSION ID:  324
ACTIVITY:  leisure
USER:  2
TIME:  2017-10-08 14:00:00


SESSION ID:  110
ACTIVITY:  eat
USER:  0
TIME:  2017-11-01 10:48:00


SESSION ID:  57
ACTIVITY:  movement
USER:  0
TIME:  2017-10-12 20:35:58


SESSION ID:  278
ACTIVITY:  sleep
USER:  2
TIME:  2017-09-30 04:00:00


SESSION ID:  58
ACTIVITY:  rest-passive
USER:  0
TIME:  2017-10-12 22:02:15


SESSION ID:  54
ACTIVITY:  rest-active
USER:  0
TIME:  2017-10-12 14:09:17


SESSION ID:  260
ACTIVITY:  household-chores
USER:  1
TIME:  2018-01-21 16:22:29


SESSION ID:  31
ACTIVITY:  focused-passive
USER:  0
TIME:  2017-10-05 14:11:55


SESSION ID:  194
ACTIVITY:  exercise
USER:  0
TIME:  2018-02-23 15:53:56


## Assessing how features evolve within a session
---

### Plotting a specific session

In [7]:
dv.full_plot_sess(df.iloc[111], fdf, RAW)

SESSION ID:  111
ACTIVITY:  exercise
USER:  0
TIME:  2017-11-01 11:29:55


### Helper to choose sessions

In [16]:
df.loc[(df.activity == 'eat') & (df.user.isin([0]))][['user', 'activity', 'start', 'duration', 'beatscount', 'rmssd', 'pnn50']].sort_values(by='pnn50', ascending=False)

user activity               start  duration  beatscount       rmssd  \
2       0      eat 2017-09-29 13:32:20       202         269  158.107901   
16      0      eat 2017-10-01 13:37:53       571         858  142.113592   
25      0      eat 2017-10-04 12:38:34       626         948  191.392030   
15      0      eat 2017-09-30 13:30:45       145         247  147.821484   
18      0      eat 2017-10-03 22:56:19       640         972  120.700624   
3       0      eat 2017-09-29 13:46:19       259         381   65.153745   
144     0      eat 2017-11-15 12:12:44       513         854   88.914662   
53      0      eat 2017-10-12 13:40:00       600         921   60.378678   
118     0      eat 2017-11-05 12:40:44       571        1007   70.780525   
158     0      eat 2017-11-23 14:29:00       466         784   40.808997   
77      0      eat 2017-10-14 14:19:41       149         252   38.239078   
126     0      eat 2017-11-07 15:35:00       314         538   51.655030   
97      0      eat 2017-10-17 15:01:39       721        1192   26.896699   
132     0      eat 2017-11-07 21:11:50       205         303   26.243195   
174     0      eat 2018-01-21 17:10:04       202         337   25.901197   
163     0      eat 2017-11-24 12:16:43       698        1372   25.596302   
138     0      eat 2017-11-09 13:18:38       156         274   25.130065   
202     0      eat 2018-04-17 18:20:49       300         558   17.582481   
102     0      eat 2017-10-31 15:29:36       297         486   14.379324   
207     0      eat 2018-04-19 14:59:34       610        1084   14.553877   
110     0      eat 2017-11-01 10:48:00       302         676   10.941596   
182     0      eat 2018-02-01 21:58:56       356         632   11.490505   
139     0      eat 2017-11-09 13:23:55       132         254   11.035695   
113     0      eat 2017-11-02 16:14:42       380         251    7.449832   
117     0      eat 2017-11-04 14:04:30       294         582   10.704126   

         pnn50  
2    46.641791  
16   33.488915  
25   29.461457  
15   26.829268  
18   23.583934  
3    13.684211  
144  12.075029  
53   11.413043  
118  10.437376  
158   9.578544  
77    9.163347  
126   7.635009  
97    5.289673  
132   4.304636  
174   3.273810  
163   3.063457  
138   1.831502  
202   1.615799  
102   1.030928  
207   1.015697  
110   0.592593  
182   0.158479  
139   0.000000  
113   0.000000  
117   0.000000

### Plotting all sessions in a filter

In [17]:
v = df[(df['activity'] == 'eat') & (df.user.isin([0])) & (df.rmssd > 64) & (df.pnn50 > 15)]
for i in range(len(v)):
    dv.full_plot_sess(v.iloc[i], fdf, RAW)

SESSION ID:  2
ACTIVITY:  eat
USER:  0
TIME:  2017-09-29 13:32:20


SESSION ID:  15
ACTIVITY:  eat
USER:  0
TIME:  2017-09-30 13:30:45


SESSION ID:  16
ACTIVITY:  eat
USER:  0
TIME:  2017-10-01 13:37:53


SESSION ID:  18
ACTIVITY:  eat
USER:  0
TIME:  2017-10-03 22:56:19


SESSION ID:  25
ACTIVITY:  eat
USER:  0
TIME:  2017-10-04 12:38:34
